In [1]:
# Ô 1: Import các thư viện lõi
import pandas as pd
import numpy as np
import requests
from datetime import datetime
import warnings

warnings.filterwarnings('ignore')
print("✅ Ô 1 chạy thành công: Thư viện lõi đã được import.")

✅ Ô 1 chạy thành công: Thư viện lõi đã được import.


In [2]:
# Ô 2: Hàm lấy dữ liệu 1 mã (từ CafeF)
def get_price_history_api(symbol: str, start_date: datetime, end_date: datetime):
    all_data = []
    page = 1
    total_pages = 1
    while page <= total_pages:
        url = "https://cafef.vn/du-lieu/Ajax/PageNew/DataHistory/PriceHistory.ashx"
        params = {"Symbol": symbol, "StartDate": start_date.strftime("%Y-%m-%d"),
                  "EndDate": end_date.strftime("%Y-%m-%d"), "PageIndex": page}
        try:
            response = requests.get(url, params=params, timeout=10)
            response.raise_for_status()
            data = response.json()
            if not data.get("Success", False): break
            records = data["Data"]["Data"]
            if not records: break
            if page == 1:
                total_count = data["Data"]["TotalCount"]
                total_pages = -(-total_count // len(records))
            all_data.extend(records)
            page += 1
        except Exception as e:
            print(f"Lỗi khi gọi API CafeF cho {symbol}: {e}")
            return None
    if not all_data: return None
    df = pd.DataFrame(all_data)
    df['Ticker'] = symbol.upper()
    numeric_columns = ['GiaDieuChinh', 'GiaDongCua', 'KhoiLuongKhopLenh', 
                      'GiaTriKhopLenh', 'GiaMoCua', 'GiaCaoNhat', 'GiaThapNhat']
    for col in numeric_columns: df[col] = pd.to_numeric(df[col], errors='coerce')
    df = df.sort_values('Ngay', ascending=True).reset_index(drop=True)
    df['GiaDongCua'].replace(0, np.nan, inplace=True); df['GiaDongCua'] = df['GiaDongCua'].ffill().bfill()
    df.loc[df['GiaDongCua'] == 0, 'GiaDieuChinh'] = df['GiaDieuChinh']
    df.loc[df['GiaDongCua'] == 0, 'GiaDongCua'] = 1
    df['adjustment_ratio'] = df['GiaDieuChinh'] / df['GiaDongCua']
    df['open_adj'] = df['GiaMoCua'] * df['adjustment_ratio']
    df['high_adj'] = df['GiaCaoNhat'] * df['adjustment_ratio']
    df['low_adj'] = df['GiaThapNhat'] * df['adjustment_ratio']
    df = df.rename(columns={'Ngay': 'time', 'open_adj': 'open', 'high_adj': 'high',
                            'low_adj': 'low', 'GiaDieuChinh': 'close', 
                            'KhoiLuongKhopLenh': 'volume', 'Ticker': 'ticker'})
    df['time'] = pd.to_datetime(df['time'], format="%d/%m/%Y")
    return df[['time', 'open', 'high', 'low', 'close', 'volume', 'ticker']].sort_values('time').reset_index(drop=True)

print("✅ Ô 2 chạy thành công: Hàm get_price_history_api đã sẵn sàng.")

✅ Ô 2 chạy thành công: Hàm get_price_history_api đã sẵn sàng.


In [3]:
# Ô 3: Hàm lấy dữ liệu nhiều mã (TỐC ĐỘ CAO - ĐA LUỒNG - THÂN THIỆN)
from concurrent.futures import ThreadPoolExecutor
import time # <-- Thêm thư viện 'time'

def get_stock_data(tickers: list, start_date: str, end_date: str) -> pd.DataFrame:
    print(f"Bắt đầu lấy dữ liệu cho {len(tickers)} mã (Đa luồng - Thân thiện)...")
    all_data = []
    start_dt = datetime.strptime(start_date, '%Y-%m-%d')
    end_dt = datetime.strptime(end_date, '%Y-%m-%d')

    # --- Logic đa luồng ---
    
    def fetch_one_ticker(ticker):
        # --------------------------------------------------
        # THAY ĐỔI CHÍNH Ở ĐÂY (Thêm 1)
        # Thêm một khoảng nghỉ nhỏ (0.2 giây) trước mỗi lần gọi API
        # để tránh bị server chặn
        # --------------------------------------------------
        time.sleep(0.2) 
        
        df_ticker = get_price_history_api(ticker, start_dt, end_dt)
        if df_ticker is not None and not df_ticker.empty:
            return df_ticker
        else:
            print(f"(!) Không tìm thấy dữ liệu cho mã: {ticker}")
            return None

    # --------------------------------------------------
    # THAY ĐỔI CHÍNH Ở ĐÂY (Thêm 2)
    # Giảm số "quầy" (workers) từ 10 xuống 5 (an toàn hơn)
    # --------------------------------------------------
    with ThreadPoolExecutor(max_workers=5) as executor:
        results = executor.map(fetch_one_ticker, tickers)
    
    # --- Kết thúc đa luồng ---

    all_data = [df for df in results if df is not None]

    if not all_data:
        print("(!) Không lấy được bất kỳ dữ liệu nào.")
        return pd.DataFrame()

    final_df = pd.concat(all_data, ignore_index=True)
    final_df = final_df.sort_values(by=['ticker', 'time']).reset_index(drop=True)
    print("✅ Lấy dữ liệu (Đa luồng) thành công!")
    return final_df

print("✅ Ô 3 chạy thành công: Hàm get_stock_data (Đa luồng - Thân thiện) đã sẵn sàng.")

✅ Ô 3 chạy thành công: Hàm get_stock_data (Đa luồng - Thân thiện) đã sẵn sàng.


In [4]:
# --- Ô 3.5 (Nâng cấp - Thêm nút "Làm mới Cache") ---

import ipywidgets as widgets
from IPython.display import display
from datetime import datetime

print("--- 1. Cấu hình Thông số ---")

# (Các widget cũ giữ nguyên)
start_date_input = widgets.DatePicker(
    description='Từ ngày', value=datetime(2018, 1, 1)
)
end_date_input = widgets.DatePicker(
    description='Đến ngày', value=datetime.now()
)
holding_period_input = widgets.Dropdown(
    options=[('3 tháng', 63), ('6 tháng', 126), ('1 năm', 252), ('2 năm', 504)],
    value=252, description='Thời hạn (Scale):'
)
risk_free_rate_input = widgets.FloatText(
    value=4.0, description='LS Phi rủi ro (%):'
)

# --------------------------------------------------
# THÊM MỚI (Để Tối ưu Tốc độ)
# --------------------------------------------------
force_refresh_checkbox = widgets.Checkbox(
    value=False,
    description='Làm mới Dữ liệu (Bỏ qua Cache & gọi lại API)',
    indent=False
)
# --------------------------------------------------

print("Vui lòng nhập các thông số bên dưới và CHẠY CÁC Ô TIẾP THEO:")
display(start_date_input, end_date_input, holding_period_input, risk_free_rate_input, force_refresh_checkbox)

--- 1. Cấu hình Thông số ---
Vui lòng nhập các thông số bên dưới và CHẠY CÁC Ô TIẾP THEO:


DatePicker(value=datetime.datetime(2018, 1, 1, 0, 0), description='Từ ngày', step=1)

DatePicker(value=datetime.datetime(2025, 11, 14, 17, 21, 41, 308639), description='Đến ngày', step=1)

Dropdown(description='Thời hạn (Scale):', index=2, options=(('3 tháng', 63), ('6 tháng', 126), ('1 năm', 252),…

FloatText(value=4.0, description='LS Phi rủi ro (%):')

Checkbox(value=False, description='Làm mới Dữ liệu (Bỏ qua Cache & gọi lại API)', indent=False)

In [5]:
pip install pyarrow

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 25.2 -> 25.3
[notice] To update, run: python.exe -m pip install --upgrade pip


In [6]:
# --- Ô 4 (Nâng cấp - Tối ưu Tốc độ bằng Caching) ---
import os # Cần thư viện 'os' để kiểm tra file

# --- 1. Đặt thông số ---
tickers_list = [
    'ACB', 'BCM', 'BID', 'BVH', 'CTG', 'FPT', 'GAS', 'GVR', 'HDB', 'HPG', 
    'LPB', 'MBB', 'MSN', 'MWG', 'PLX', 'SAB', 'SHB', 'SSB', 'SSI', 'STB', 
    'TCB', 'TPB', 'VCB', 'VHM', 'VIB', 'VIC', 'VJC', 'VNM', 'VPB', 'VRE'
]
CACHE_FILE = 'vn30_data_cache.parquet' # Tên file cache

# --- 2. Đọc thông số từ Widget ---
try:
    start_time = start_date_input.value.strftime('%Y-%m-%d')
    end_time = end_date_input.value.strftime('%Y-%m-%d')
    FORCE_REFRESH = force_refresh_checkbox.value
except NameError:
    print("LỖI: Không tìm thấy widget. Vui lòng chạy lại Ô 3.5!")
    raise

# --- 3. Logic Caching ---
if os.path.exists(CACHE_FILE) and not FORCE_REFRESH:
    
    # --- LUỒNG NHANH (0.1 giây) ---
    print(f"--- Đang tải dữ liệu từ Cache ({CACHE_FILE}) ---")
    raw_data = pd.read_parquet(CACHE_FILE)
    print("✅ Tải từ Cache thành công!")

else:
    # --- LUỒNG CHẬM (10-30 giây) ---
    if FORCE_REFRESH:
        print("--- Bắt buộc làm mới (Force Refresh) ---")
    else:
        print("--- Lần chạy đầu tiên (Cache not found) ---")

    print(f"--- Đang lấy dữ liệu cho {len(tickers_list)} mã VN30 (Đa luồng) ---")
    print(f"--- Khung thời gian: {start_time} đến {end_time} ---")

    # Gọi hàm đa luồng (từ Ô 3)
    raw_data = get_stock_data(tickers_list, start_time, end_time)

    # 4. Hiển thị kết quả và LƯU VÀO CACHE
    if not raw_data.empty:
        print(f"\nTổng số {len(raw_data)} dòng dữ liệu đã được tải.")
        
        # Lưu vào Cache
        try:
            print(f"--- Đang lưu vào Cache ({CACHE_FILE}) ---")
            raw_data.to_parquet(CACHE_FILE)
            print("✅ Dữ liệu đã tải và lưu vào Cache.")
        except Exception as e:
            print(f"LỖI khi lưu Cache: {e}")
            print("Vui lòng cài đặt 'pip install pyarrow'")
            
    else:
        print("\n(!) Không tải được dữ liệu cho khung thời gian này.")

# --- 5. Báo cáo cuối cùng ---
if 'raw_data' in locals() and not raw_data.empty:
     print("\n✅ Dữ liệu đã sẵn sàng cho Ô 5.")

--- Lần chạy đầu tiên (Cache not found) ---
--- Đang lấy dữ liệu cho 30 mã VN30 (Đa luồng) ---
--- Khung thời gian: 2018-01-01 đến 2025-11-14 ---
Bắt đầu lấy dữ liệu cho 30 mã (Đa luồng - Thân thiện)...
✅ Lấy dữ liệu (Đa luồng) thành công!

Tổng số 55270 dòng dữ liệu đã được tải.
--- Đang lưu vào Cache (vn30_data_cache.parquet) ---
✅ Dữ liệu đã tải và lưu vào Cache.

✅ Dữ liệu đã sẵn sàng cho Ô 5.


In [7]:
# Ô 5: Tính Tỷ suất sinh lời

if 'raw_data' not in locals() or raw_data.empty:
    print("LỖI: Biến 'raw_data' không tồn tại. Vui lòng chạy lại Ô 4.")
else:
    # Xóa trùng lặp
    raw_data.drop_duplicates(subset=['time', 'ticker'], keep='last', inplace=True)
    
    # Xoay bảng
    price_pivot = raw_data.pivot(
        index='time', columns='ticker', values='close'
    )
    
    # Tính Lợi nhuận Đơn (theo CSLT.docx)
    returns_df_raw = price_pivot.pct_change()

    # Xóa hàng đầu tiên (luôn là NaN)
    returns_df = returns_df_raw.iloc[1:]

    print("\n--- Bảng Tỷ suất sinh lời (Lợi nhuận Đơn) ---")
    display(returns_df.head())
    print("\n✅ Ô 5 chạy thành công! 'returns_df' đã sẵn sàng.")


--- Bảng Tỷ suất sinh lời (Lợi nhuận Đơn) ---


ticker           ACB  BCM  BID  BVH  CTG       FPT  GAS  GVR       HDB  \
time                                                                     
2018-05-04  0.002381  NaN  NaN  NaN  NaN       NaN  NaN  NaN       NaN   
2018-05-07  0.054632  NaN  NaN  NaN  NaN       NaN  NaN  NaN       NaN   
2018-05-08 -0.012387  NaN  NaN  NaN  NaN       NaN  NaN  NaN       NaN   
2018-05-09 -0.022805  NaN  NaN  NaN  NaN       NaN  NaN  NaN       NaN   
2018-05-10 -0.044341  NaN  NaN  NaN  NaN -0.001296  NaN  NaN -0.067925   

ticker           HPG  ...  TCB  TPB       VCB  VHM  VIB       VIC       VJC  \
time                  ...                                                     
2018-05-04       NaN  ...  NaN  NaN       NaN  NaN  NaN       NaN       NaN   
2018-05-07       NaN  ...  NaN  NaN       NaN  NaN  NaN       NaN       NaN   
2018-05-08       NaN  ...  NaN  NaN       NaN  NaN  NaN       NaN       NaN   
2018-05-09       NaN  ...  NaN  NaN       NaN  NaN  NaN       NaN       NaN   
2018-05-10 -0.031481  ...  NaN  NaN -0.050517  NaN  NaN -0.019493 -0.010872   

ticker           VNM       VPB  VRE  
time                                 
2018-05-04       NaN       NaN  NaN  
2018-05-07       NaN       NaN  NaN  
2018-05-08       NaN       NaN  NaN  
2018-05-09       NaN       NaN  NaN  
2018-05-10 -0.027024 -0.058824  0.0  

[5 rows x 30 columns]


✅ Ô 5 chạy thành công! 'returns_df' đã sẵn sàng.


In [8]:
# Ô 6: Định nghĩa hàm calculate_stats
def calculate_stats(returns_df: pd.DataFrame, he_so_scale: int) -> (pd.Series, pd.DataFrame):
    # .mean() và .cov() của Pandas tự động bỏ qua NaN (skipna=True)
    expected_returns = returns_df.mean() * he_so_scale
    cov_matrix = returns_df.cov() * he_so_scale
    return expected_returns, cov_matrix

print("✅ Ô 6 chạy thành công: Hàm calculate_stats đã sẵn sàng.")

✅ Ô 6 chạy thành công: Hàm calculate_stats đã sẵn sàng.


In [9]:
# Ô 7: Chạy tính Stats

try:
    HE_SO_SCALE = holding_period_input.value 
except NameError:
    print("LỖI: Vui lòng chạy lại Ô 3.5!")
    HE_SO_SCALE = 252

expected_returns, cov_matrix = calculate_stats(returns_df, HE_SO_SCALE)

print(f"--- LỢI NHUẬN KỲ VỌNG (Scale: {HE_SO_SCALE} ngày) ---")
display(expected_returns.head())
print(f"\n--- MA TRẬN HIỆP PHƯƠNG SAI (Scale: {HE_SO_SCALE} ngày) ---")
display(cov_matrix.head())
print("\n✅ Ô 7 chạy thành công!")

--- LỢI NHUẬN KỲ VỌNG (Scale: 252 ngày) ---


ticker
ACB    0.188669
BCM    0.251087
BID    0.160505
BVH    0.006236
CTG    0.187157
dtype: float64


--- MA TRẬN HIỆP PHƯƠNG SAI (Scale: 252 ngày) ---


ticker       ACB       BCM       BID       BVH       CTG       FPT       GAS  \
ticker                                                                         
ACB     0.086125  0.032839  0.063906  0.042847  0.068727  0.043759  0.038220   
BCM     0.032839  0.168878  0.035134  0.036248  0.038385  0.031041  0.037395   
BID     0.063906  0.035134  0.115519  0.053888  0.082271  0.045583  0.048818   
BVH     0.042847  0.036248  0.053888  0.113859  0.051963  0.040118  0.045455   
CTG     0.068727  0.038385  0.082271  0.051963  0.115877  0.047969  0.046927   

ticker       GVR       HDB       HPG  ...       TCB       TPB       VCB  \
ticker                                ...                                 
ACB     0.051016  0.056044  0.051564  ...  0.061927  0.051635  0.040988   
BCM     0.052888  0.035744  0.035286  ...  0.036312  0.034065  0.022721   
BID     0.054097  0.059841  0.057091  ...  0.063904  0.052740  0.049506   
BVH     0.062923  0.042457  0.048958  ...  0.046549  0.039276  0.033570   
CTG     0.059121  0.064311  0.060864  ...  0.071332  0.059423  0.048860   

ticker       VHM       VIB       VIC       VJC       VNM       VPB       VRE  
ticker                                                                        
ACB     0.034622  0.057948  0.023042  0.023623  0.025895  0.065167  0.041303  
BCM     0.035063  0.035999  0.026217  0.019997  0.021953  0.038955  0.040867  
BID     0.039090  0.057162  0.027745  0.026770  0.031084  0.066636  0.053710  
BVH     0.037458  0.043373  0.031984  0.026598  0.032185  0.048909  0.044317  
CTG     0.040819  0.062584  0.031526  0.024224  0.028185  0.074693  0.054666  

[5 rows x 30 columns]


✅ Ô 7 chạy thành công!


In [10]:
# Ô 7.5: Phân tích Thống kê Mô tả
import plotly.graph_objects as go 

if 'returns_df' not in locals():
    print("LỖI: Không tìm thấy 'returns_df'. Vui lòng chạy lại Ô 5.")
else:
    # 1. Bảng Thống kê
    print("\n--- Bảng Thống kê Mô tả Tỷ suất sinh lời ---")
    stats_table = returns_df.describe()
    display(stats_table.style.format("{:.2%}"))

    # 2. Ma trận Tương quan & Heatmap
    print("\n--- Ma trận Tương quan & Heatmap ---")
    correlation_matrix = returns_df.corr()
    
    # Hiển thị bảng (dùng thang đo chuẩn)
    display(correlation_matrix.style
            .format("{:.3f}")
            .background_gradient(cmap='RdBu_r', vmin=-1, vmax=1))

    # Vẽ Heatmap (ĐÃ SỬA: Xóa texttemplate vì 30x30 quá rối)
    labels = correlation_matrix.columns
    fig_heatmap = go.Figure(data=go.Heatmap(
        z=correlation_matrix.values, x=labels, y=labels,
        colorscale='RdBu_r', zmin=-1, zmax=1,
        hoverongaps=False
    ))
    fig_heatmap.update_layout(
        title='Heatmap Ma trận Tương quan (VN30)', template='plotly_dark',
        height=700, width=800, # Tăng kích thước
        yaxis_autorange='reversed'
    )
    fig_heatmap.show()
    print("\n✅ Ô 7.5 chạy thành công!")


--- Bảng Thống kê Mô tả Tỷ suất sinh lời ---



--- Ma trận Tương quan & Heatmap ---



✅ Ô 7.5 chạy thành công!


In [11]:
# Ô 8: Định nghĩa hàm run_monte_carlo_sim

import plotly.express as px
import plotly.io as pio # <--- DÒNG NÀY ĐÃ ĐƯỢC THÊM VÀO

pio.templates.default = "plotly_dark" # <-- Lỗi đã xảy ra ở đây

# Cần hàm get_portfolio_stats (từ Ô 10) chạy trước
# Vui lòng chạy Ô 10 trước khi chạy Ô 9

def run_monte_carlo_sim(n_sims: int, 
                        expected_returns: pd.Series, 
                        cov_matrix: pd.DataFrame, 
                        risk_free_rate: float) -> pd.DataFrame:
    """
    Chạy mô phỏng Monte Carlo (ĐÃ SỬA: dùng risk_free_rate)
    """
    print(f"Bắt đầu chạy {n_sims} mô phỏng Monte Carlo (với Rf = {risk_free_rate:.2%})...")
    
    num_assets = len(expected_returns)
    results = np.zeros((3, n_sims))
    weights_record = []
    
    # Cần đảm bảo Ô 10 đã chạy (để có hàm get_portfolio_stats)
    try:
        get_portfolio_stats
    except NameError:
        print("LỖI: Không tìm thấy hàm 'get_portfolio_stats'. Vui lòng chạy Ô 10 trước!")
        return pd.DataFrame() # Trả về DF rỗng
    
    for i in range(n_sims):
        weights = np.random.random(num_assets)
        weights /= np.sum(weights)
        weights_record.append(weights)
        
        port_return, port_risk, port_sharpe = get_portfolio_stats(
            weights, expected_returns, cov_matrix, risk_free_rate
        )
        
        results[0, i] = port_return
        results[1, i] = port_risk
        results[2, i] = port_sharpe

    results_df = pd.DataFrame(results.T, columns=['Return', 'Risk', 'Sharpe'])
    weights_df = pd.DataFrame(weights_record, columns=expected_returns.index)
    sim_data_df = pd.concat([results_df, weights_df], axis=1)
    
    print("✅ Mô phỏng hoàn thành!")
    return sim_data_df

print("✅ Ô 8 chạy thành công: Hàm run_monte_carlo_sim đã sẵn sàng.")
print("‼️ CẢNH BÁO: Vui lòng chạy Ô 10 (bên dưới) trước khi chạy Ô 9.")

✅ Ô 8 chạy thành công: Hàm run_monte_carlo_sim đã sẵn sàng.
‼️ CẢNH BÁO: Vui lòng chạy Ô 10 (bên dưới) trước khi chạy Ô 9.


In [12]:
# Ô 10: Định nghĩa Hàm Tối ưu hóa
from scipy.optimize import minimize

try:
    RISK_FREE_RATE = risk_free_rate_input.value / 100.0
    print(f"--- Đã lấy Lãi suất Phi rủi ro: {RISK_FREE_RATE:.2%} ---")
except NameError:
    print("LỖI: Vui lòng chạy lại Ô 3.5!")
    RISK_FREE_RATE = 0.04

# Hàm 1: Stats (Đã sửa: dùng Rf)
def get_portfolio_stats(weights: np.array, 
                        expected_returns: pd.Series, 
                        cov_matrix: pd.DataFrame, 
                        risk_free_rate: float) -> tuple:
    port_return = np.sum(weights * expected_returns)
    port_risk = np.sqrt(np.dot(weights.T, np.dot(cov_matrix, weights)))
    port_sharpe = (port_return - risk_free_rate) / port_risk 
    return (port_return, port_risk, port_sharpe)

# Hàm 2: Max Sharpe (Đã sửa: dùng Rf)
def minimize_negative_sharpe(weights: np.array, 
                             expected_returns: pd.Series, 
                             cov_matrix: pd.DataFrame,
                             risk_free_rate: float) -> float:
    return -get_portfolio_stats(weights, expected_returns, cov_matrix, risk_free_rate)[2]

# Hàm 3: Min Risk
def minimize_portfolio_risk(weights: np.array, 
                            expected_returns: pd.Series, 
                            cov_matrix: pd.DataFrame,
                            risk_free_rate: float) -> float:
    return get_portfolio_stats(weights, expected_returns, cov_matrix, risk_free_rate)[1]

print("✅ Ô 10 chạy thành công: Các hàm Tối ưu hóa đã sẵn sàng.")

--- Đã lấy Lãi suất Phi rủi ro: 4.00% ---
✅ Ô 10 chạy thành công: Các hàm Tối ưu hóa đã sẵn sàng.


In [13]:
# Ô 9: Chạy Monte Carlo

# SỬA: Giảm xuống 10,000 (vì 30 mã rất chậm)
N_SIMULATIONS = 10000 

if 'expected_returns' in locals():
    sim_data_df = run_monte_carlo_sim(
        N_SIMULATIONS, 
        expected_returns, 
        cov_matrix, 
        RISK_FREE_RATE
    )
    
    print("\n--- 5 danh mục mô phỏng mẫu ---")
    display(sim_data_df.head())

    # Vẽ biểu đồ nền
    fig = px.scatter(
        sim_data_df, x='Risk', y='Return', color='Sharpe',
        color_continuous_scale='Viridis',
        hover_data=sim_data_df.columns,
        title=f'Đường biên Hiệu quả - {N_SIMULATIONS} danh mục (VN30, Rf={RISK_FREE_RATE:.1%})'
    )
    fig.update_layout(xaxis_tickformat='.1%', yaxis_tickformat='.1%')
    fig.show()
else:
    print("LỖI: Không tìm thấy 'expected_returns'. Vui lòng chạy lại Ô 7.")

Bắt đầu chạy 10000 mô phỏng Monte Carlo (với Rf = 4.00%)...
✅ Mô phỏng hoàn thành!

--- 5 danh mục mô phỏng mẫu ---


Return      Risk    Sharpe       ACB       BCM       BID       BVH  \
0  0.158013  0.215160  0.548488  0.007253  0.068579  0.012298  0.017144   
1  0.162705  0.215501  0.569396  0.062584  0.016502  0.054240  0.044945   
2  0.165305  0.214574  0.583969  0.020677  0.052900  0.027208  0.016576   
3  0.167819  0.219824  0.581462  0.022730  0.000158  0.045981  0.025859   
4  0.175081  0.225924  0.597907  0.000563  0.031707  0.050581  0.006569   

        CTG       FPT       GAS  ...       TCB       TPB       VCB       VHM  \
0  0.072481  0.005139  0.031566  ...  0.006522  0.051926  0.021886  0.063655   
1  0.034679  0.058890  0.039734  ...  0.034666  0.010679  0.030633  0.003005   
2  0.028664  0.048890  0.037225  ...  0.044166  0.007608  0.050312  0.032688   
3  0.000619  0.058566  0.018559  ...  0.054200  0.034490  0.063849  0.019766   
4  0.012694  0.063734  0.023389  ...  0.017528  0.056325  0.000514  0.055504   

        VIB       VIC       VJC       VNM       VPB       VRE  
0  0.010781  0.027411  0.036366  0.055497  0.060093  0.025107  
1  0.032182  0.030798  0.060702  0.035521  0.030504  0.017178  
2  0.049475  0.013400  0.028400  0.051977  0.042107  0.036696  
3  0.013990  0.007069  0.041472  0.002689  0.038656  0.022117  
4  0.043077  0.011238  0.057382  0.014111  0.045441  0.053110  

[5 rows x 33 columns]

In [14]:
# Ô 11: Chạy Tối ưu hóa

print("--- Đang chạy tối ưu hóa... ---")

if 'sim_data_df' not in locals():
    print("LỖI: Không tìm thấy 'sim_data_df'. Vui lòng chạy lại Ô 9.")
else:
    num_assets = len(expected_returns)
    args = (expected_returns, cov_matrix, RISK_FREE_RATE)
    constraints = ({'type': 'eq', 'fun': lambda x: np.sum(x) - 1})
    bounds = tuple((0.0, 1.0) for _ in range(num_assets))

    # 1. Tìm Bảo thủ (dùng điểm đoán từ Monte)
    min_vol_guess_weights = sim_data_df.loc[sim_data_df['Risk'].idxmin()].values[3:]
    opt_min_vol = minimize(
        minimize_portfolio_risk, min_vol_guess_weights, args=args,
        method='SLSQP', bounds=bounds, constraints=constraints
    )
    min_vol_weights = opt_min_vol.x
    min_vol_stats = get_portfolio_stats(min_vol_weights, expected_returns, cov_matrix, RISK_FREE_RATE)

    # 2. Tìm Cân bằng (dùng điểm đoán từ Monte)
    max_sharpe_guess_weights = sim_data_df.loc[sim_data_df['Sharpe'].idxmax()].values[3:]
    opt_max_sharpe = minimize(
        minimize_negative_sharpe, max_sharpe_guess_weights, args=args,
        method='SLSQP', bounds=bounds, constraints=constraints
    )
    max_sharpe_weights = opt_max_sharpe.x
    max_sharpe_stats = get_portfolio_stats(max_sharpe_weights, expected_returns, cov_matrix, RISK_FREE_RATE)

    # 3. Tìm Mạo hiểm
    max_ret_weights = np.zeros(num_assets)
    max_ret_index = expected_returns.argmax()
    max_ret_weights[max_ret_index] = 1.0
    max_ret_stats = get_portfolio_stats(max_ret_weights, expected_returns, cov_matrix, RISK_FREE_RATE)
    
    print("\n✅ Tối ưu hóa hoàn thành!")
    
    # 4. Hiển thị Bảng
    optimal_weights_df = pd.DataFrame({
        'Bảo thủ (Min Risk)': min_vol_weights,
        'Cân bằng (Max Sharpe)': max_sharpe_weights,
        'Mạo hiểm (Max Return)': max_ret_weights
    }, index=expected_returns.index)

    # Chỉ hiển thị các mã có tỷ trọng > 0.1%
    display(optimal_weights_df[(optimal_weights_df > 0.001).any(axis=1)]
            .style.format("{:.2%}"))

    optimal_stats_dict = {
        'min_vol': min_vol_stats,
        'max_sharpe': max_sharpe_stats,
        'max_ret': max_ret_stats
    }

--- Đang chạy tối ưu hóa... ---

✅ Tối ưu hóa hoàn thành!


In [15]:
# Ô 11.5: Vẽ Tỷ trọng (Biểu đồ Cột)

if 'optimal_weights_df' not in locals():
    print("LỖI: Vui lòng chạy lại Ô 11.")
else:
    print("--- Đang vẽ Biểu đồ Cột Phân bổ Tỷ trọng (Module 4) ---")
    
    # Lọc ra các mã có tỷ trọng > 0.1% (để biểu đồ sạch)
    df_plot = optimal_weights_df[(optimal_weights_df > 0.001).any(axis=1)].copy()
    
    # --------------------------------------------------
    # SỬA LỖI KEYERROR Ở ĐÂY
    # --------------------------------------------------
    # Chuyển đổi sang format "dài"
    df_plot_long = df_plot.reset_index().melt(
        id_vars='ticker', # <-- Sửa 'index' thành 'ticker'
        var_name='Danh mục', 
        value_name='Tỷ trọng'
    )
    # Đổi tên cột 'ticker' cho đẹp
    df_plot_long.rename(columns={'ticker': 'Mã CP'}, inplace=True)
    # --------------------------------------------------
    
    # Vẽ biểu đồ cột nhóm
    fig_bars = px.bar(
        df_plot_long,
        x='Danh mục',
        y='Tỷ trọng',
        color='Mã CP', # Mỗi mã 1 màu
        text_auto='.2%',
        title='Phân bổ Tỷ trọng Tối ưu theo 3 Khẩu vị Rủi ro (Chỉ hiển thị mã > 0.1%)'
    )
    
    fig_bars.update_layout(template='plotly_dark', yaxis_tickformat='.0%')
    fig_bars.show()

--- Đang vẽ Biểu đồ Cột Phân bổ Tỷ trọng (Module 4) ---


In [16]:
# Ô 12: Vẽ Đường biên Hoàn chỉnh

if 'fig' not in locals():
    print("LỖI: Vui lòng chạy lại Ô 9.")
else:
    print("--- Đang thêm các điểm Tối ưu, Cổ phiếu Đơn lẻ VÀ Đường CAL ---")
    
    # 1. Thêm 3 Ngôi sao
    stats_min_vol = optimal_stats_dict['min_vol']
    stats_max_sharpe = optimal_stats_dict['max_sharpe']
    stats_max_ret = optimal_stats_dict['max_ret']
    
    fig.add_trace(go.Scatter(x=[stats_min_vol[1]], y=[stats_min_vol[0]], mode='markers', marker=dict(color='white', size=12, symbol='star', line=dict(color='black', width=2)), name='Bảo thủ (Min Risk)'))
    fig.add_trace(go.Scatter(x=[stats_max_sharpe[1]], y=[stats_max_sharpe[0]], mode='markers', marker=dict(color='cyan', size=12, symbol='star', line=dict(color='black', width=2)), name='Cân bằng (Max Sharpe)'))
    fig.add_trace(go.Scatter(x=[stats_max_ret[1]], y=[stats_max_ret[0]], mode='markers', marker=dict(color='red', size=12, symbol='star', line=dict(color='black', width=2)), name='Mạo hiểm (Max Return)'))
    
    # 2. Thêm Cổ phiếu Đơn lẻ
    asset_returns = expected_returns
    asset_risks = np.sqrt(np.diag(cov_matrix))
    asset_names = expected_returns.index
    fig.add_trace(go.Scatter(x=asset_risks, y=asset_returns, mode='markers', marker=dict(color='orange', size=8, symbol='diamond'), text=asset_names, name='Cổ phiếu Đơn lẻ'))
    
    # 3. Vẽ Đường CAL
    sharpe_risk = stats_max_sharpe[1]
    sharpe_return = stats_max_sharpe[0]
    x_cal = [0, sharpe_risk * 1.5] 
    y_cal = [RISK_FREE_RATE, (sharpe_return - RISK_FREE_RATE) / sharpe_risk * (sharpe_risk * 1.5) + RISK_FREE_RATE]
    
    fig.add_trace(go.Scatter(x=x_cal, y=y_cal, mode='lines', line=dict(color='lime', width=2, dash='dash'), name='Đường Phân bổ Vốn (CAL)'))

    # 4. Cập nhật Layout (Sửa lỗi Chú thích)
    fig.update_layout(
        title='Biểu đồ Đường biên Hiệu quả Toàn diện (có CAL)',
        legend=dict(orientation="h", yanchor="bottom", y=-0.2, xanchor="center", x=0.5),
        margin=dict(b=100)
    )
    fig.update_yaxes(range=[min(0, RISK_FREE_RATE * 0.9), max(asset_returns.max(), stats_max_ret[0]) * 1.1])
    fig.update_xaxes(range=[0, asset_risks.max() * 1.1])
    
    fig.show()

--- Đang thêm các điểm Tối ưu, Cổ phiếu Đơn lẻ VÀ Đường CAL ---


In [ ]:
# Ô 13: Định nghĩa hàm Backtest
import quantstats as qs

def run_simple_backtest(daily_returns_df: pd.DataFrame, 
                        portfolio_weights: np.array) -> (pd.Series, pd.Series):
    port_returns_daily = daily_returns_df.dot(portfolio_weights)
    port_returns_daily = pd.Series(port_returns_daily, index=daily_returns_df.index)
    cumulative_returns = (1 + port_returns_daily).cumprod()
    return port_returns_daily, cumulative_returns

print("✅ Ô 13 chạy thành công: Hàm run_simple_backtest đã sẵn sàng.")

✅ Ô 13 chạy thành công: Hàm run_simple_backtest đã sẵn sàng.


In [23]:
# Ô 14: Chạy Backtest
print("--- Đang chạy Backtest cho 3 danh mục... ---")

if 'optimal_weights_df' not in locals():
    print("LỖI: Vui lòng chạy lại Ô 11.")
else:
    weights_min_vol = optimal_weights_df['Bảo thủ (Min Risk)'].values
    weights_max_sharpe = optimal_weights_df['Cân bằng (Max Sharpe)'].values
    weights_max_ret = optimal_weights_df['Mạo hiểm (Max Return)'].values

    returns_min_vol, cum_min_vol = run_simple_backtest(returns_df, weights_min_vol)
    returns_max_sharpe, cum_max_sharpe = run_simple_backtest(returns_df, weights_max_sharpe)
    returns_max_ret, cum_max_ret = run_simple_backtest(returns_df, weights_max_ret)
    
    all_cumulative_df = pd.DataFrame({
        'Bảo thủ (Min Risk)': cum_min_vol,
        'Cân bằng (Max Sharpe)': cum_max_sharpe,
        'Mạo hiểm (Max Return)': cum_max_ret
    })
    all_returns_df = pd.DataFrame({
        'Bảo thủ (Min Risk)': returns_min_vol,
        'Cân bằng (Max Sharpe)': returns_max_sharpe,
        'Mạo hiểm (Max Return)': returns_max_ret
    })
    
    print("✅ Backtest hoàn thành!")
    display(all_cumulative_df.tail())

--- Đang chạy Backtest cho 3 danh mục... ---
✅ Backtest hoàn thành!


Bảo thủ (Min Risk)  Cân bằng (Max Sharpe)  Mạo hiểm (Max Return)
time                                                                        
2025-11-10            1.233970               2.967534               4.419030
2025-11-11            1.241157               2.957148               4.345837
2025-11-12            1.265180               3.054117               4.451052
2025-11-13            1.276061               3.043622               4.473925
2025-11-14            1.276594               3.078705               4.565416

In [19]:
# Ô 15: Vẽ Biểu đồ Backtest
print("--- Đang vẽ biểu đồ tăng trưởng... ---")

fig_backtest = px.line(
    all_cumulative_df, 
    title=f'So sánh Hiệu quả Tăng trưởng (Từ {start_time})'
)
fig_backtest.update_layout(
    template='plotly_dark', 
    yaxis_title='Giá trị Danh mục (Bắt đầu từ 1.0)', 
    legend_title='Danh mục'
)
fig_backtest.show()

--- Đang vẽ biểu đồ tăng trưởng... ---


In [20]:
# Ô 16: Tính Bảng Metrics
print("--- Đang tính toán các chỉ số hiệu suất ---")

metrics = ['Tổng Lợi nhuận (Cumulative)', 'Lợi nhuận TB Năm (Annualized)', 
           'Rủi ro Năm (Annualized)', 'Mức sụt giảm Tối đa (Max Drawdown)', 
           'Chỉ số Sharpe (Historical)']
summary_table = pd.DataFrame(index=metrics) 

if 'all_returns_df' not in locals():
    print("LỖI: Không tìm thấy 'all_returns_df'. Vui lòng chạy lại Ô 14.")
else:
    for port_name in all_returns_df.columns:
        returns_series = all_returns_df[port_name]
        summary_table.loc['Tổng Lợi nhuận (Cumulative)', port_name] = qs.stats.comp(returns_series)
        summary_table.loc['Lợi nhuận TB Năm (Annualized)', port_name] = qs.stats.cagr(returns_series)
        summary_table.loc['Rủi ro Năm (Annualized)', port_name] = qs.stats.volatility(returns_series)
        summary_table.loc['Mức sụt giảm Tối đa (Max Drawdown)', port_name] = qs.stats.max_drawdown(returns_series)
        summary_table.loc['Chỉ số Sharpe (Historical)', port_name] = qs.stats.sharpe(returns_series, rf=RISK_FREE_RATE) # Dùng Rf

    print("\n--- BẢNG TỔNG KẾT CHỈ SỐ HIỆU SUẤT ---")
    
    # Sửa lỗi format
    percent_rows = summary_table.index.difference(['Chỉ số Sharpe (Historical)'])
    number_row = pd.Index(['Chỉ số Sharpe (Historical)'])
    styler = summary_table.style
    styler.format('{:,.2%}', subset=(percent_rows, slice(None)))
    styler.format('{:,.2f}', subset=(number_row, slice(None)))
    display(styler)

--- Đang tính toán các chỉ số hiệu suất ---

--- BẢNG TỔNG KẾT CHỈ SỐ HIỆU SUẤT ---


In [21]:
# Ô 16.5: Vẽ Biểu đồ Metrics (Đã tách)
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.express as px

# Kiểm tra xem 'summary_table' đã tồn tại chưa
if 'summary_table' not in locals():
    print("LỖI: Không tìm thấy 'summary_table'. Vui lòng chạy lại Ô 16.")
else:
    print("--- Đang vẽ Biểu đồ Cột so sánh Hiệu suất (Đã tách) ---")
    
    # 1. Chuẩn bị dữ liệu (Lấy tên các danh mục)
    port_names = summary_table.columns
    
    # 2. Tạo 3 biểu đồ con (3 hàng, 1 cột)
    fig_metrics = make_subplots(
        rows=3, cols=1,
        shared_xaxes=True, # Dùng chung trục X (tên danh mục)
        vertical_spacing=0.1,
        subplot_titles=("So sánh Lợi nhuận", 
                        "So sánh Rủi ro", 
                        "So sánh Tỷ lệ (Sharpe)")
    )

    # --- Biểu đồ 1: LỢI NHUẬN ---
    return_metrics = ['Tổng Lợi nhuận (Cumulative)', 'Lợi nhuận TB Năm (Annualized)']
    for metric in return_metrics:
        fig_metrics.add_trace(go.Bar(
            x=port_names,
            y=summary_table.loc[metric],
            text=summary_table.loc[metric],
            texttemplate='%{y:.2%}', # Format %
            name=metric
        ), row=1, col=1)

    # --- Biểu đồ 2: RỦI RO ---
    risk_metrics = ['Rủi ro Năm (Annualized)', 'Mức sụt giảm Tối đa (Max Drawdown)']
    for metric in risk_metrics:
        fig_metrics.add_trace(go.Bar(
            x=port_names,
            y=summary_table.loc[metric],
            text=summary_table.loc[metric],
            texttemplate='%{y:.2%}', # Format %
            name=metric
        ), row=2, col=1)

    # --- Biểu đồ 3: TỶ LỆ SHARPE ---
    sharpe_metric = 'Chỉ số Sharpe (Historical)'
    fig_metrics.add_trace(go.Bar(
        x=port_names,
        y=summary_table.loc[sharpe_metric],
        text=summary_table.loc[sharpe_metric],
        texttemplate='%{y:.2f}', # Format SỐ (vd: 0.45)
        name=sharpe_metric
    ), row=3, col=1)
    
    # --- 3. Cập nhật Layout chung ---
    fig_metrics.update_layout(
        height=1000, # Tăng chiều cao
        template='plotly_dark',
        barmode='group', # Đặt các cột cạnh nhau
        legend_title_text='Chỉ số',
        title_text='Phân tích Chi tiết Hiệu suất Backtest'
    )
    
    # Cập nhật trục Y cho từng biểu đồ
    fig_metrics.update_yaxes(title_text='Lợi nhuận', tickformat='.0%', row=1, col=1)
    fig_metrics.update_yaxes(title_text='Rủi ro', tickformat='.0%', row=2, col=1)
    fig_metrics.update_yaxes(title_text='Tỷ lệ', tickformat='.2f', row=3, col=1)

    fig_metrics.show()

--- Đang vẽ Biểu đồ Cột so sánh Hiệu suất (Đã tách) ---
